#Setup

In [1]:
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
from matplotlib.pyplot import figure
import seaborn as sns
import pandas as pd
import operator
from math import log
from pandas import Series, DataFrame
from pylab import rcParams
import pyreadr

import sklearn
from sklearn import metrics 
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split, cross_val_score

from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import KFold # import KFold
from sklearn import datasets

from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.gaussian_process.kernels import RBF
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import precision_recall_fscore_support
from sklearn.linear_model import LogisticRegression

from matplotlib.lines import Line2D
import re
import pickle

/Users/Abood/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


In [2]:
passing_grades = ["A+", "A", "A-", "B+", "B", "B-", "C+", "C", "C-", "D+", "D",
                  "D-", "S", "CR"]
letter_grades = ["A+", "A", "A-", "B+", "B", "B-", "C+", "C", "C-", "D+", "D",
                  "D-", "NP", "W"]
passing_pattern = r"A[+-]*|B[+-]*|C[+-]*|D[+-]*|S|CR"
success_grades = ["A+", "A", "A-", "B+"]
DATA_PATH = "../data"

# Dataset of the last 5 years record

In [3]:
raw_data = pd.read_csv('../data/clean_full.csv', header=0)
raw_data = raw_data.drop(['Unnamed: 0'], axis=1)
raw_data.columns

Index(['acad_career', 'strm', 'stdnt_enrl_status', 'unt_taken', 'unt_billing',
       'crse_grade_input', 'earn_credit', 'emplid', 'subject', 'catalog_nbr',
       'crse_acad_org', 'sex'],
      dtype='object')

Winter is 4, Spring is 6, Fall is 2, Summer is 8?
e.g. 1198 is 18-19, summer quarter. 1196 is 18-19, spring quarter

In [4]:
def get_course_name (row):
    if row['subject'] != None and row['catalog_nbr'] != None:
        return row['subject']+row['catalog_nbr']
    return ""
def dropped_function (row):
    if row['stdnt_enrl_status'] == 'D':
        return 1
    return 0

In [46]:
def getStudentFeatures(subject, number, select_majors=False):
    course_entries = raw_data.loc[(raw_data['subject'] == subject) & (raw_data['catalog_nbr'] == number) & # all course entries that are about the certain course we want
                                  (raw_data['strm'] >= 1162) & # taken in 15-16 fall or later
                                  ((raw_data['crse_grade_input'].isin(letter_grades)) | (raw_data['strm'] == 1204)) & #Grade needs to be a letter or it's the latest quarter (nan)
                                  (raw_data['strm'] != 1168) & (raw_data['strm'] != 1178) & (raw_data['strm'] != 1188) &
                                  (raw_data['strm'] != 1198) & (raw_data['stdnt_enrl_status'] != 'D')] # not dropped and not summer
#     return course_entries
    students = course_entries.emplid # Students from the course entries
    students_prev_classes = raw_data.loc[raw_data['emplid'].isin(students)] # Other classes taken by these students
    if select_majors:
        students_prev_classes = students_prev_classes.loc[students_prev_classes['subject'].isin(['CME', 'CS', 'EE', 'MATH', 'STATS'])]
    possible_prev_classes = students_prev_classes.apply(lambda row: get_course_name(row), axis=1) # List of courses taken by these students
    if len(possible_prev_classes) == 0:
        return possible_prev_classes
    possible_prev_classes = possible_prev_classes.unique().tolist() # Focus on unique courses
    possible_prev_classes.append("strm") # For now add term to the data of when the course was taken
    possible_prev_classes.append("female") # Add gender
    possible_prev_classes.append("emplid") # Add emplid
    possible_prev_classes.append("y") # Add the target to the data. Will split it later
    a = np.zeros(shape=(len(course_entries),len(possible_prev_classes))) # all 0 initialized features matrix. +2 for female and strm
    dataset = pd.DataFrame(a,columns=possible_prev_classes) # same as above, but in pandas to allow indexing by course name
    print('looping on course ', subject, number)
    for counter, idx in enumerate(course_entries.index): # loop over all class entried
        grade = course_entries.loc[[idx]]['crse_grade_input']
        print('On student number ', counter, 'of: ', len(course_entries))
        gradeStr = grade.tolist()[0]
        if (gradeStr == "A+" or gradeStr == "A" or
          gradeStr == "A-" or gradeStr == "B+"):
            dataset['y'][counter] = 1
        # fill predictor matrix X
        std_id = course_entries.loc[[idx]]['emplid'] # Get the student id
        quarter = course_entries.loc[[idx]]['strm'] # Get the term
        female = course_entries.loc[[idx]]['sex'] # Get the student gender
        student_courses = students_prev_classes.loc[students_prev_classes['emplid'] == std_id.tolist()[0]] # Get all courses the student took
        student_courses = student_courses.loc[student_courses['strm'] < quarter.tolist()[0]] # Filter the courses to be only before the course of interest
        if select_majors:
            student_courses = student_courses.loc[student_courses['subject'].isin(['CME', 'CS', 'EE', 'MATH', 'STATS'])]
        if (female.tolist()[0] == 'M'):
            dataset["female"][counter] = 0
        else:
            dataset["female"][counter] = 1
        dataset["strm"][counter] = quarter.tolist()[0]
        dataset["emplid"][counter] = std_id.tolist()[0]
        for j in student_courses.index:# Loop over the student's courses
            course_name = student_courses.loc[[j]]['subject']+student_courses.loc[[j]]['catalog_nbr'] # Get the course name
            grade = student_courses.loc[[j]]['crse_grade_input']
            gradeStr = grade.tolist()[0]
            if (gradeStr == "A+" or gradeStr == "A" or
                gradeStr == "A-" or gradeStr == "B+"):
                dataset.iloc[counter, dataset.columns.get_loc(course_name.tolist()[0])] = 1 # Set the course name in X to the new value (or if it was already passed keep the value)
#             dev_break = True
#         break
    return dataset

# Try sklearn logistic regression

In [47]:
# Use the X predictor matrix and y outcome vector from 
# getStudentFeatures, fit a logistic regression model and return
# the list of coefficients, default sorted by absolute value

# Params: sort = ["pos", "neg", "abs"] to sort by largest positive, negative, or
# absolute value of coefficients
def get_coefs(X_train, X_test, y_train, y_test, result_vec, sort = "abs"):
    model = LogisticRegression(solver="lbfgs")
    model.fit(X_train, y_train)
    train_score = model.score(X_train,y_train) 
    test_score = model.score(X_test,y_test)
    result_vec['train_score'] = train_score
    result_vec['test_score'] = test_score
    print("training accuracy: %s" % train_score)
    print("test accuracy: %s" % test_score)
    coefs = [(X_test.columns[i], model.coef_[0][i]) for i in range(len(X_test.columns))]
    if sort:
        if sort == "pos":
            coefs = sorted(coefs, key = lambda x: x[1], reverse = True)
        if sort == "neg":
            coefs = sorted(coefs, key = lambda x: x[1], reverse = False)
        if sort == "abs":
            coefs = sorted(coefs, key = lambda x: abs(x[1]), reverse = True)
    return coefs

In [48]:
def get_and_split_data(subject, course_nbr, test_quarters, result_vec):
    #For now, dropping this quarter
    validation = raw_data.loc[(raw_data['subject'] == subject) & (raw_data['catalog_nbr'] == course_nbr) & (raw_data['strm'].isin(test_quarters))]
    if len(validation) == 0:
        return {}, {}, {}, {}
    validation = raw_data.loc[(raw_data['subject'] == subject) & (raw_data['catalog_nbr'] == course_nbr) & (~raw_data['strm'].isin(test_quarters))]
    if len(validation) == 0:
        return {}, {}, {}, {}
    dataset = getStudentFeatures(subject, course_nbr)
    if dataset.empty:
        return {}, {}, {}, {}
    dataset_grades = dataset.loc[dataset['strm'] < 1204.0]
    dataset_train = dataset_grades.loc[~dataset_grades['strm'].isin(test_quarters)]
    dataset_test = dataset_grades.loc[dataset_grades['strm'].isin(test_quarters)]

    dataset_train = dataset_train.drop(["strm", "emplid"], axis=1)
    dataset_test = dataset_test.drop(["strm", "emplid"], axis=1)

    result_vec['size'] = len(dataset)
    if len(dataset_grades) == 0:
        result_vec['ground_truth'] = 0
    else:
        result_vec['ground_truth'] = len(dataset_grades.loc[(dataset_grades['y']) == 1]) / len(dataset_grades)
    X_train = dataset_train.drop(["y"], axis=1)
    y_train = dataset_train["y"]
    X_test = dataset_test.drop(["y"], axis=1)
    y_test = dataset_test["y"]
    
    if len(y_train) == 0:
        result_vec['train_ground_truth'] = 0
    else:
        result_vec['train_ground_truth'] = len(y_train.loc[y_train == 1]) / len(y_train)
    
    if len(y_test) == 0:
        result_vec['test_ground_truth'] = 0
    else:
        result_vec['test_ground_truth'] = len(y_test.loc[y_test == 1]) / len(y_test)
    result_vec['train_size'] = len(X_train)
    result_vec['test_size'] = len(X_test)
    
    return X_train, X_test, y_train, y_test

In [49]:
courses = raw_data.loc[(raw_data['strm'] == 1194) | (raw_data['strm'] == 1196)]
courses = courses.drop(['acad_career', 'strm', 'stdnt_enrl_status', 'unt_taken', 'unt_billing',
                        'crse_grade_input', 'earn_credit', 'emplid', 'crse_acad_org', 'sex'], axis=1)
courses

subject catalog_nbr
25             EE         390
26             CS         161
27       SPANLANG        12SL
28           CHEM         141
29           CHEM         141
...           ...         ...
2667867  TIBETLNG           3
2667868  INTNLREL         102
2667869     STATS          60
2667870     THINK          43
2667871     THINK          43

[97324 rows x 2 columns]

In [ ]:
results = {}
seen_classes = {}

In [ ]:
for index, row in courses.iterrows():
    course_number = row['subject'] + row['catalog_nbr']
    if course_number in seen_classes:
        continue
    seen_classes[course_number] = 1    
    temp = {}
    print(course_number)
    X_train, X_test, y_train, y_test = get_and_split_data(row['subject'], row['catalog_nbr'], [1194.0, 1196.0], temp)
    if len(y_test) == 0 or len(y_test.unique()) == 1:
        continue
    try:
        coefs = get_coefs(X_train, X_test, y_train, y_test, temp, 'abs')
        for coef in coefs:
            temp[coef[0]] = coef[1]
        results[course_number] = temp
        print('done')
    except:
        print('failed on ', course_number)

HISTORY145B
looping on course  HISTORY 145B
On student number  0 of:  30
On student number  1 of:  30
On student number  2 of:  30
On student number 

/Users/Abood/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/Abood/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/Abood/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:42: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/Abood/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:43:

 3 of:  30


/Users/Abood/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


On student number  4 of:  30
On student number  5 of:  30
On student number  6 of:  30
On student number  7 of:  30
On student number  8 of:  30
On student number  9 of:  30
On student number  10 of:  30
On student number  11 of:  30
On student number  12 of:  30
On student number  13 of:  30
On student number  14 of:  30
On student number  15 of:  30
On student number  16 of:  30
On student number  17 of:  30
On student number  18 of:  30
On student number  19 of:  30
On student number  20 of:  30
On student number  21 of:  30
On student number  22 of:  30
On student number  23 of:  30
On student number  24 of:  30
On student number  25 of:  30
On student number  26 of:  30
On student number  27 of:  30
On student number  28 of:  30
On student number  29 of:  30
HISTORY36S
looping on course  HISTORY 36S
On student number  0 of:  6
On student number  1 of:  6
On student number  2 of:  6
On student number  3 of:  6
On student number  4 of:  6
On student number  5 of:  6
failed on  HISTO

...

On student number  111 of:  540
On student number  112 of:  540
On student number  113 of:  540
On student number  114 of:  540
On student number  115 of:  540
On student number  116 of:  540
On student number  117 of:  540
On student number  118 of:  540
On student number  119 of:  540
On student number  120 of:  540
On student number  121 of:  540
On student number  122 of:  540
On student number  123 of:  540
On student number  124 of:  540
On student number  125 of:  540
On student number  126 of:  540
On student number  127 of:  540
On student number  128 of:  540
On student number  129 of:  540
On student number  130 of:  540
On student number  131 of:  540
On student number  132 of:  540
On student number  133 of:  540
On student number  134 of:  540
On student number  135 of:  540
On student number  136 of:  540
On student number  137 of:  540
On student number  138 of:  540
On student number  139 of:  540
On student number  140 of:  540
On student number  141 of:  540
On stude

On student number  368 of:  540
On student number  369 of:  540
On student number  370 of:  540
On student number  371 of:  540
On student number  372 of:  540
On student number  373 of:  540
On student number  374 of:  540
On student number  375 of:  540
On student number  376 of:  540
On student number  377 of:  540
On student number  378 of:  540
On student number  379 of:  540
On student number  380 of:  540
On student number  381 of:  540
On student number  382 of:  540
On student number  383 of:  540
On student number  384 of:  540
On student number  385 of:  540
On student number  386 of:  540
On student number  387 of:  540
On student number  388 of:  540
On student number  389 of:  540
On student number  390 of:  540
On student number  391 of:  540
On student number  392 of:  540
On student number  393 of:  540
On student number  394 of:  540
On student number  395 of:  540
On student number  396 of:  540
On student number  397 of:  540
On student number  398 of:  540
On stude

On student number  54 of:  118
On student number  55 of:  118
On student number  56 of:  118
On student number  57 of:  118
On student number  58 of:  118
On student number  59 of:  118
On student number  60 of:  118
On student number  61 of:  118
On student number  62 of:  118
On student number  63 of:  118
On student number  64 of:  118
On student number  65 of:  118
On student number  66 of:  118
On student number  67 of:  118
On student number  68 of:  118
On student number  69 of:  118
On student number  70 of:  118
On student number  71 of:  118
On student number  72 of:  118
On student number  73 of:  118
On student number  74 of:  118
On student number  75 of:  118
On student number  76 of:  118
On student number  77 of:  118
On student number  78 of:  118
On student number  79 of:  118
On student number  80 of:  118
On student number  81 of:  118
On student number  82 of:  118
On student number  83 of:  118
On student number  84 of:  118
On student number  85 of:  118
On stude

On student number  8 of:  87
On student number  9 of:  87
On student number  10 of:  87
On student number  11 of:  87
On student number  12 of:  87
On student number  13 of:  87
On student number  14 of:  87
On student number  15 of:  87
On student number  16 of:  87
On student number  17 of:  87
On student number  18 of:  87
On student number  19 of:  87
On student number  20 of:  87
On student number  21 of:  87
On student number  22 of:  87
On student number  23 of:  87
On student number  24 of:  87
On student number  25 of:  87
On student number  26 of:  87
On student number  27 of:  87
On student number  28 of:  87
On student number  29 of:  87
On student number  30 of:  87
On student number  31 of:  87
On student number  32 of:  87
On student number  33 of:  87
On student number  34 of:  87
On student number  35 of:  87
On student number  36 of:  87
On student number  37 of:  87
On student number  38 of:  87
On student number  39 of:  87
On student number  40 of:  87
On student n

On student number  185 of:  237
On student number  186 of:  237
On student number  187 of:  237
On student number  188 of:  237
On student number  189 of:  237
On student number  190 of:  237
On student number  191 of:  237
On student number  192 of:  237
On student number  193 of:  237
On student number  194 of:  237
On student number  195 of:  237
On student number  196 of:  237
On student number  197 of:  237
On student number  198 of:  237
On student number  199 of:  237
On student number  200 of:  237
On student number  201 of:  237


In [61]:
len(results)

23

In [62]:
predicts = pd.DataFrame.from_dict(results, orient='index').fillna(0)
predicts.to_csv('../data/partial-1.csv')